In [1]:
#Python Libs
import sys
import os
import glob
from datetime import datetime
import json
import urllib
import time
import os
import requests
import http.client



#Data Analysis Libs
import pandas as pd
import numpy as np

In [3]:
#Constants
MIN_NUM_ARGS = 4
first_cols = ['cardNum', 'boarding_datetime','gps_datetime','route','busCode','stopPointId']
boarding_key_cols = ['cardNum','boarding_datetime']
gps_key_cols = ['route','busCode','tripNum','stopPointId']
sort_cols = boarding_key_cols + gps_key_cols[:-1] + ['gps_datetime']
max_match_diff = 1800

In [4]:
#Functions
def printUsage():
    print ("Usage: " + sys.argv[0] + " <enhanced-buste-folder-path> <output-folder-path> <otp-server-url> <initial-date> <final-date>")
    
def get_otp_itineraries(otp_url,o_lat,o_lon,d_lat,d_lon,date,time,route,verbose=False):
    otp_http_request = 'routers/cg/plan?fromPlace={},{}&toPlace={},{}&mode=TRANSIT,WALK&date={}&time={}&numItineraries=500&maxWalkingDistance=1000'
    
    otp_request_url = otp_url + otp_http_request.format(o_lat,o_lon,d_lat,d_lon,date.strip(),time,route)
    print(otp_request_url)

    if verbose:
        print (otp_request_url)

    return json.loads(urllib.urlopen(otp_request_url).read())

In [5]:
def get_otp_suggested_trips(od_matrix,otp_url):
    
    req_duration = []
    trips_otp_response = {}
    counter = 0
    for index, row in od_matrix.iterrows():
        id=float(row['stopPointId'])
        date = row['gps_datetime'].strftime('%Y-%m-%d ')
        
        start_time = (row['gps_datetime']-pd.Timedelta('3 h')-pd.Timedelta('2 min')).strftime('%H:%M:%S')
        
        req_start_time = time.time()
        #UFCG -7.217167, -35.908995
        #print(row['gpsLat'])
        #print(row['gpsLon'])
        trip_plan = get_otp_itineraries(otp_url,row['shapeLat'], row['shapeLon'], row['gpsLat'], row['gpsLon'], date,start_time, row['route'])
        #print(trip_plan)
        req_end_time = time.time()
        req_time = req_end_time - req_start_time
        req_duration.append((id,req_time))
        print("OTP request took ", req_end_time - req_start_time,"seconds.")
        trips_otp_response[id] = trip_plan
        counter+=1

        req_dur_df = pd.DataFrame().from_records(req_duration,columns=['id','duration'])
    print (req_dur_df.duration.describe())	

    return trips_otp_response

In [6]:
def extract_otp_trips_legs(otp_trips):
    trips_legs = []

    for trip in otp_trips.keys():
        if 'plan' in otp_trips[trip]:
            itinerary_id = 1
            for itinerary in otp_trips[trip]['plan']['itineraries']:
                date = otp_trips[trip]['plan']['date']/1000
                leg_id = 1
                for leg in itinerary['legs']:
                    route = leg['route'] if leg['route'] != '' else None
                    fromStopId = leg['from']['stopId'].split(':')[1] if leg['mode'] == 'BUS' else None
                    toStopId = leg['to']['stopId'].split(':')[1] if leg['mode'] == 'BUS' else None
                    start_time = long(leg['startTime'])/1000
                    end_time = long(leg['endTime'])/1000
                    duration = (end_time - start_time)/60
                    trips_legs.append((date,trip,itinerary_id,leg_id,start_time,end_time,leg['mode'],route,fromStopId,toStopId, duration))
                    
                    leg_id += 1
                itinerary_id += 1
    return trips_legs

In [7]:
def prepare_otp_legs_df(otp_legs_list):
    labels=['date','user_trip_id','itinerary_id','leg_id','otp_start_time','otp_end_time','mode','route','from_stop_id','to_stop_id','otp_duration_mins']
    return pd.DataFrame.from_records(data=otp_legs_list, columns=labels) \
                    .assign(date = lambda x: pd.to_datetime(x['date'],unit='s').dt.strftime('%Y-%m-%d'),
                            otp_duration_mins = lambda x : (x['otp_end_time'] - x['otp_start_time'])/60,
                            route = lambda x : (x['route']),
                            from_stop_id = lambda x : pd.to_numeric(x['from_stop_id'],errors='coerce'),
                            to_stop_id = lambda x : pd.to_numeric(x['to_stop_id'],errors='coerce')) \
                    .assign(otp_start_time = lambda x : pd.to_datetime(x['otp_start_time'], unit='s'),
                            otp_end_time = lambda x : pd.to_datetime(x['otp_end_time'], unit='s')) \
                    .sort_values(by=['date','user_trip_id','itinerary_id','otp_start_time'])

In [9]:
#Teste para verificar a montagem de itinerários para todos ônibus da cidade
user_trips_file = os.getcwd() + "/data/input/2019_02_01_bus_trips.csv"
output_folder_path = os.getcwd() + "/data/output/" 
otp_server_url = "http://localhost:5601/otp/"

print ("Processing file", user_trips_file)
file_name = user_trips_file.split('/')[-1].replace('.csv','')
file_date = pd.to_datetime(file_name.split('_bus_trips')[0],format='%Y_%m_%d')
if (file_date.dayofweek == 6):
    print ("File date is sunday. File will not be processed.")
else:
    try:
        user_trips = pd.read_csv(user_trips_file, low_memory=False)
        # Filtering just trips starting from Hector's home (bus stop)
        user_trips = user_trips.loc[(user_trips['gps_datetime'] != '-')] 
        user_trips['gps_datetime'] = pd.to_datetime(user_trips['gps_datetime'], format='%d-%m-%Y %H:%M:%S')
        otp_suggestions = get_otp_suggested_trips(user_trips,otp_server_url)
        otp_legs_df = prepare_otp_legs_df(extract_otp_trips_legs(otp_suggestions))
        otp_legs_df.drop_duplicates(subset=['date','user_trip_id','leg_id','otp_end_time','mode', 'route','otp_duration_mins', 'from_stop_id', 'to_stop_id'], inplace=True)

        
        otp_legs_df.to_csv(output_folder_path + '/' + file_name + '_otp_itineraries.csv',index=False)
    except Exception as e:
        print (e)
        print ("Error in processing file " + file_name)

('Processing file', '/home/hector/TransferTimeAnalysisCG/workspace/python/people-paths/trips-destination-inference/data/input/2019_02_01_bus_trips.csv')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24269,-35.92352&toPlace=-7.242401,-35.92365&mode=TRANSIT,WALK&date=2019-02-01&time=02:16:58&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 4.943948984146118, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24447,-35.92281&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=02:17:45&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.043699026107788086, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24517,-35.92448&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=02:18:04&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.029842138290405273, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24556,-35.92619&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=02:18:23&numItinerarie

('OTP request took ', 3.286794900894165, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22667,-35.89908&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=02:47:40&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.011778831481933594, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22882,-35.9043&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=02:47:47&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.012512922286987305, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.21814,-35.88114&toPlace=-7.218123,-35.88103&mode=TRANSIT,WALK&date=2019-02-01&time=02:48:07&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 3.3469929695129395, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.21928,-35.88337&toPlace=-7.219279,-35.88343&mode=TRANSIT,WALK&date=2019-02-01&time=02:50:10&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.01526498794555664, 'seconds.')

('OTP request took ', 2.6962759494781494, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24727,-35.92123&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=03:25:01&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.008457183837890625, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24657,-35.91894&toPlace=-7.246613,-35.9189&mode=TRANSIT,WALK&date=2019-02-01&time=03:25:54&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 5.543655157089233, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24643,-35.91621&toPlace=-7.246466,-35.9161&mode=TRANSIT,WALK&date=2019-02-01&time=03:27:26&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 5.538465976715088, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24644,-35.91278&toPlace=-7.24645,-35.91275&mode=TRANSIT,WALK&date=2019-02-01&time=03:28:58&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.01685500144958496, 

('OTP request took ', 5.530880928039551, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.23622,-35.92117&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=04:09:22&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.008684158325195312, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.23686,-35.92266&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=04:09:54&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.009187936782836914, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.23913,-35.92762&toPlace=-7.239105,-35.92783&mode=TRANSIT,WALK&date=2019-02-01&time=04:10:47&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 1.755444049835205, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.23836,-35.92612&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=04:10:54&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.007311105728149414, 'seconds.')
http://localho

('OTP request took ', 4.051507949829102, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.2265,-35.89899&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=04:43:51&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.007924079895019531, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22667,-35.89908&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=04:43:59&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.007061004638671875, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22505,-35.89561&toPlace=-7.225108,-35.89565&mode=TRANSIT,WALK&date=2019-02-01&time=04:46:02&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 3.7788820266723633, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22059,-35.88981&toPlace=-7.220601,-35.88969&mode=TRANSIT,WALK&date=2019-02-01&time=04:49:36&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.011388063430786133, 'seconds.'

...

('OTP request took ', 0.00985407829284668, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.21828,-35.92105&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=18:56:14&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.006470918655395508, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22074,-35.89507&toPlace=-7.220885,-35.89447&mode=TRANSIT,WALK&date=2019-02-01&time=18:56:25&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.01209712028503418, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22158,-35.89182&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=18:57:03&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.0054700374603271484, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22056,-35.88986&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=18:57:54&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.006206035614013672, 'seconds.')
http://lo

('OTP request took ', 4.174515962600708, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.22807,-35.92137&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=19:46:49&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.0056171417236328125, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.23251,-35.92122&toPlace=-7.232507,-35.92096&mode=TRANSIT,WALK&date=2019-02-01&time=19:48:27&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 2.1523168087005615, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.23038,-35.92413&toPlace=-7.230396,-35.92417&mode=TRANSIT,WALK&date=2019-02-01&time=19:49:59&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 5.5308051109313965, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.23075,-35.92499&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=19:50:08&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.006014823913574219, 'seconds.'

('OTP request took ', 5.5257909297943115, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.24685,-35.9207&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=04:39:22&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.006535053253173828, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.21915,-35.88329&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=04:40:39&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.006242990493774414, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.21844,-35.88153&toPlace=-7.217913,-35.88067&mode=TRANSIT,WALK&date=2019-02-01&time=04:41:51&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 5.529098987579346, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.2174,-35.87961&toPlace=-7.217588,-35.87985&mode=TRANSIT,WALK&date=2019-02-01&time=04:42:22&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 5.121996164321899, 'seconds.')
ht

('OTP request took ', 2.186959981918335, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.2523,-35.93611&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=05:11:49&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.0041539669036865234, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.25271,-35.93605&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=05:12:36&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.004284858703613281, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.25524,-35.93549&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=05:16:40&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.004621982574462891, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.2586,-35.93532&toPlace=-,-&mode=TRANSIT,WALK&date=2019-02-01&time=05:23:36&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.004575014114379883, 'seconds.')
http://localhost:5601/otp/ro

KeyboardInterrupt: 

In [17]:
#user_trips.dtypes
user_trips = gps_trips.loc[(user_trips['gps_datetime'] != '-')]
user_trips['gps_datetime'] = pd.to_datetime(user_trips['gps_datetime'], format='%d-%m-%Y %H:%M:%S')
user_trips.head()

route tripNum  shapeId  routeFrequency  shapeSequence  shapeLat  \
16933   944       1    72976  high_frequency             40  -7.28659   
17061   944       2    72976  high_frequency             40  -7.28659   
17110   944       3    72976  high_frequency             40  -7.28659   
17143   944       4    72976  high_frequency             40  -7.28659   
17220   944       5    72976  high_frequency             40  -7.28659   

       shapeLon  distanceTraveledShape busCode gpsPointId     gpsLat  \
16933 -35.89567                 1398.0    1051          -          -   
17061 -35.89567                 1398.0    1051      54143  -7.286596   
17110 -35.89567                 1398.0    1051          -          -   
17143 -35.89567                 1398.0    1051      66914  -7.286622   
17220 -35.89567                 1398.0    1051          -          -   

          gpsLon distanceToShapePoint        gps_datetime  stopPointId  \
16933          -                    - 2019-02-01 07:52:12       491551   
17061  -35.89565            2.3046215 2019-02-01 10:23:59       491551   
17110          -                    - 2019-02-01 11:06:17       491551   
17143  -35.89559             9.514184 2019-02-01 11:31:50       491551   
17220          -                    - 2019-02-01 13:24:14       491551   

      streetName     problem  
16933          -     BETWEEN  
17061          -  NO_PROBLEM  
17110          -     BETWEEN  
17143          -  NO_PROBLEM  
17220          -     BETWEEN

In [12]:
user_trips_file = os.getcwd() + "/data/input/2019_02_01_bus_trips.csv"
output_folder_path = os.getcwd() + "/data/output/" 
otp_server_url = "http://localhost:5601/otp/"

print ("Processing file", user_trips_file)
file_name = user_trips_file.split('/')[-1].replace('.csv','')
file_date = pd.to_datetime(file_name.split('_bus_trips')[0],format='%Y_%m_%d')
if (file_date.dayofweek == 6):
    print ("File date is sunday. File will not be processed.")
else:
    try:
        user_trips = pd.read_csv(user_trips_file, low_memory=False)
        # Filtering just trips starting from Hector's home (bus stop)
        gps_trips = user_trips.loc[(user_trips['stopPointId'] == 491551)]
        gps_trips = gps_trips.loc[(gps_trips['gps_datetime'] != '-')] 
        gps_trips['gps_datetime'] = pd.to_datetime(gps_trips['gps_datetime'], format='%d-%m-%Y %H:%M:%S')
        #print(gps_trips.head())
        otp_suggestions = get_otp_suggested_trips(gps_trips,otp_server_url)
        otp_legs_df = prepare_otp_legs_df(extract_otp_trips_legs(otp_suggestions))
        otp_legs_df.drop_duplicates(subset=['date','user_trip_id','leg_id','otp_end_time','mode', 'route','otp_duration_mins', 'from_stop_id', 'to_stop_id'], inplace=True)

        
        otp_legs_df.to_csv(output_folder_path + '/' + file_name + '_otp_itineraries.csv',index=False)
    except Exception as e:
        print (e)
        print ("Error in processing file " + file_name)


('Processing file', '/home/hector/TransferTimeAnalysisCG/workspace/python/people-paths/trips-destination-inference/data/input/2019_02_01_bus_trips.csv')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.28659,-35.89567&toPlace=-7.217167,-35.908995&mode=TRANSIT,WALK&date=2019-02-01&time=04:50:12&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.4292581081390381, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.28659,-35.89567&toPlace=-7.217167,-35.908995&mode=TRANSIT,WALK&date=2019-02-01&time=07:21:59&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.0747530460357666, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.28659,-35.89567&toPlace=-7.217167,-35.908995&mode=TRANSIT,WALK&date=2019-02-01&time=08:04:17&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.10241103172302246, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.28659,-35.89567&toPlace=-7.217167,-35.908995&mode=TRANSI

('OTP request took ', 0.08926892280578613, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.28659,-35.89567&toPlace=-7.217167,-35.908995&mode=TRANSIT,WALK&date=2019-02-01&time=16:38:28&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.0867011547088623, 'seconds.')
http://localhost:5601/otp/routers/cg/plan?fromPlace=-7.28659,-35.89567&toPlace=-7.217167,-35.908995&mode=TRANSIT,WALK&date=2019-02-01&time=17:42:34&numItineraries=500&maxWalkingDistance=1000
('OTP request took ', 0.09114694595336914, 'seconds.')
count    35.000000
mean      0.111887
std       0.060820
min       0.074753
25%       0.085949
50%       0.095134
75%       0.112807
max       0.429258
Name: duration, dtype: float64
